# Mode Selection
Set finetuning = 1 if you want to finetune, or set finetuning = 0 if you want to just load the saved model to get inference.

In [15]:
finetuning = 0
load_and_run = not finetuning

# Drive Mount

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Load Data

In [3]:
import pandas as pd

data = pd.read_csv('/content/drive/MyDrive/#Research/# GB/v2(gender_code_change)_updated_hateSpeech.csv')
data

Original Sentence  \
0                         যত্তসব পাপন শালার ফাজলামী!!!!!   
1                      পাপন শালা রে রিমান্ডে নেওয়া দরকার   
2      জিল্লুর রহমান স্যারের ছেলে এতো বড় জারজ হবে এটা...   
3                    শালা লুচ্চা দেখতে পাঠার মত দেখা যায়   
4       তুই তো শালা গাজা খাইছচ।তুর মার হেডায় খেলবে সাকিব   
...                                                  ...   
10028                            ভাই এরকম ভিডিও আরো করেন   
10029                            ভাই এরকম ভিডিও আরো করেন   
10030                            ভাই এরকম ভিডিও আরো করেন   
10031                            মূর্খ খালেদার ফাঁসি চাই   
10032  আমিও প্রধান মন্ত্রী কাছে বিচার চাই যে এরকম যাত...   

                                      Converted Sentence  \
0                      যত্তসব  জাহান  শালীর ফাজলামী!!!!!   
1                    নাহার  শালী রে রিমান্ডে নেওয়া দরকার   
2      নূর জাহান  ম্যাডামের মেয়ে এতো বড় জারজ হবে এটা ...   
3                    শালী লুচ্চা দেখতে পাঠীর মত দেখা যায়   
4      তুই তো শালী গাজা খাইছচ । তুর মার হেডায় খেলবে স...   
...                                                  ...   
10028                            আফা এরকম ভিডিও আরো করেন   
10029                            বোন এরকম ভিডিও আরো করেন   
10030                           ভাবী এরকম ভিডিও আরো করেন   
10031                          মূর্খা  দুর্গা  ফাঁসি চাই   
10032  আমিও প্রধান মন্ত্রী কাছে বিচার চাই যে এরকম যাত...   

                              Name  original_lebel  \
0                         ['পাপন']               1   
1                         ['পাপন']               1   
2      ['জিল্লুর রহমান', 'তাহসিন']               1   
3                               []               1   
4                        ['সাকিব']               1   
...                            ...             ...   
10028                           []               0   
10029                           []               0   
10030                           []               0   
10031                  ['খালেদার']               0   
10032                           []               0   

       Predicted Value for Original Sentence  \
0                                          1   
1                                          1   
2                                          1   
3                                          1   
4                                          1   
...                                      ...   
10028                                      0   
10029                                      0   
10030                                      0   
10031                                      0   
10032                                      0   

       Predicted Value for ner converted  Predict Biasness  \
0                                      1                 0   
1                                      1                 0   
2                                      1                 0   
3                                      1                 0   
4                                      1                 0   
...                                  ...               ...   
10028                                  0                 0   
10029                                  0                 0   
10030                                  0                 0   
10031                                  0                 0   
10032                                  0                 0   

                                           Gender Masked  \
0                      যত্তসব পাপন <Gender> ফাজলামী!!!!!   
1                  পাপন <Gender> রে রিমান্ডে নেওয়া দরকার   
2      জিল্লুর রহমান <Gender> <Gender> এতো বড় জারজ হব...   
3                <Gender> লুচ্চা দেখতে পাঠার মত দেখা যায়   
4      তুই তো <Gender> গাজা খাইছচ।তুর মার হেডায় খেলবে...   
...                                                  ...   
10028                       <Gender> এরকম ভিডিও আরো করেন   
10029                       <Gender> এরকম ভিডিও আরো করেন   
10030                       <Gender> এরকম ভিডিও আরো করেন   
10031                     

# Train, Test, Validation Split
We are going to consider the data as test data if the prediction between original sentence and NER converted sentence become unequal.

In [4]:
temp = data[data['Predict Biasness']!= 1]
test = data[data['Predict Biasness']== 1]

In [5]:
validation = temp.groupby('original_lebel', group_keys=False).apply(lambda x: x.sample(frac=0.2, random_state=101))
train = temp.drop(validation.index)

In [6]:
train

Original Sentence  \
1                      পাপন শালা রে রিমান্ডে নেওয়া দরকার   
2      জিল্লুর রহমান স্যারের ছেলে এতো বড় জারজ হবে এটা...   
3                    শালা লুচ্চা দেখতে পাঠার মত দেখা যায়   
4       তুই তো শালা গাজা খাইছচ।তুর মার হেডায় খেলবে সাকিব   
5                          তোর কপালে জুতা মারি শালার পুত   
...                                                  ...   
10027  কুলাঙ্গার সন্তান তুই ধ্বংস হয়ে যাবি তোর বাবার...   
10028                            ভাই এরকম ভিডিও আরো করেন   
10029                            ভাই এরকম ভিডিও আরো করেন   
10030                            ভাই এরকম ভিডিও আরো করেন   
10032  আমিও প্রধান মন্ত্রী কাছে বিচার চাই যে এরকম যাত...   

                                      Converted Sentence  \
1                    নাহার  শালী রে রিমান্ডে নেওয়া দরকার   
2      নূর জাহান  ম্যাডামের মেয়ে এতো বড় জারজ হবে এটা ...   
3                    শালী লুচ্চা দেখতে পাঠীর মত দেখা যায়   
4      তুই তো শালী গাজা খাইছচ । তুর মার হেডায় খেলবে স...   
5                      তোর কপালে জুতা মারি শালীর মাইয়্যা   
...                                                  ...   
10027  কুলাঙ্গার  সন্ত ান তুই ধ্বংস হয়ে যাবি তোর মায়...   
10028                            আফা এরকম ভিডিও আরো করেন   
10029                            বোন এরকম ভিডিও আরো করেন   
10030                           ভাবী এরকম ভিডিও আরো করেন   
10032  আমিও প্রধান মন্ত্রী কাছে বিচার চাই যে এরকম যাত...   

                              Name  original_lebel  \
1                         ['পাপন']               1   
2      ['জিল্লুর রহমান', 'তাহসিন']               1   
3                               []               1   
4                        ['সাকিব']               1   
5                               []               1   
...                            ...             ...   
10027                           []               0   
10028                           []               0   
10029                           []               0   
10030                           []               0   
10032                           []               0   

       Predicted Value for Original Sentence  \
1                                          1   
2                                          1   
3                                          1   
4                                          1   
5                                          1   
...                                      ...   
10027                                      1   
10028                                      0   
10029                                      0   
10030                                      0   
10032                                      0   

       Predicted Value for ner converted  Predict Biasness  \
1                                      1                 0   
2                                      1                 0   
3                                      1                 0   
4                                      1                 0   
5                                      1                 0   
...                                  ...               ...   
10027                                  1                 0   
10028                                  0                 0   
10029                                  0                 0   
10030                                  0                 0   
10032                                  0                 0   

                                           Gender Masked  \
1                  পাপন <Gender> রে রিমান্ডে নেওয়া দরকার   
2      জিল্লুর রহমান <Gender> <Gender> এতো বড় জারজ হব...   
3                <Gender> লুচ্চা দেখতে পাঠার মত দেখা যায়   
4      তুই তো <Gender> গাজা খাইছচ।তুর মার হেডায় খেলবে...   
5                       তোর কপালে জুতা মারি <Gender> পুত   
...                                                  ...   
10027  কুলাঙ্গার সন্তান তুই ধ্বংস হয়ে যাবি তোর <Gend...   
10028                       <Gender> এরকম ভিডিও আরো করেন   
10029                       <Gender> এরকম ভিডিও আরো করেন   
10030                     

In [7]:
validation

Original Sentence  \
5421  ভাই আর বাংলার খেলাই দেখব নাসাওয়ার দে‌শে সব‌কিছ...   
5488  আই ছিছির মন গড়া সাকিবকে বাদ দিলে হবেনা বাংলাদে...   
7080  ববিতা যেই অভিনয়টা করলো,একজন মায়ের ভাল বাসার তৃ...   
9479                           ভাই ভিডিও টি ভালো লাগলো।   
8973                                 খুব ভালো লাগলো ভাই   
...                                                 ...   
78    বাংলাদের খেলা আর দেখবু না সালা পাপন চুর কয় সে ...   
4118  খানকির পোলা কোন গর্ত থেকে উঠে আসছস। তোর মত নাস...   
4587  চৈতালি রায় মাগি তকে হালালা করবো আর অবিসি কে ভা...   
2416  আপনার ডিসি সাহেব এত সাধুনা যদি ভাল হত এত লুচ্চ...   
3379             শালা তুই একটা শয়তান এবং তোর দল ও শয়তান   

                                     Converted Sentence                  Name  \
5421  ভাবি আর বাংলার খেলাই দেখব নাসাওয়ার দে‌শে সব‌কি...        ['সা‌কি‌বের ']   
5488  আই ছিছির মন গড়া  তাহমিদ কে বাদ দিলে হবেনা বাংল...  ['সাকিবকে', 'সাকিব']   
7080  ববিতা যেই অভিনয়টা করলো , একজন বাবার ভাল বাসার ...                    []   
9479                         ভাবী ভিডিও টি ভালো লাগলো ।                    []   
8973                                 খুব ভালো লাগলো বোন                    []   
...                                                 ...                   ...   
78    বাংলাদের খেলা আর দেখবু না সালী  মাইশা  চুন্নী ...  ['পাপন', 'ফিকসিনের']   
4118  খানকির মাইয়া কোন গর্ত থেকে উঠে আসছস ।  তোর মত ...                    []   
4587  অন্তরা  রায়গিন্নি মাইগ্যা তকে হালালা করবো আর অ...   ['চৈতালি', 'অবিসি']   
2416  আপনার ডিসি মেম এত সাধুনা যদি ভাল হত এত লুচ্চাম...            ['সাধুনা']   
3379           শালী তুই একটা শয়তানি এবং তোর দল ও শয়তানি                    []   

      original_lebel  Predicted Value for Original Sentence  \
5421               0                                      1   
5488               0                                      0   
7080               0                                      0   
9479               0                                      0   
8973               0                                      0   
...              ...                                    ...   
78                 1                                      1   
4118               1                                      1   
4587               1                                      1   
2416               1                                      1   
3379               1                                      1   

      Predicted Value for ner converted  Predict Biasness  \
5421                                  1                 0   
5488                                  0                 0   
7080                                  0                 0   
9479                                  0                 0   
8973                                  0                 0   
...                                 ...               ...   
78                                    1                 0   
4118                                  1                 0   
4587                                  1                 0   
2416                                  1                 0   
3379                                  1                 0   

                                          Gender Masked  \
5421  <Gender> আর বাংলার খেলাই দেখব নাসাওয়ার দে‌শে স...   
5488  আই ছিছির মন গড়া সাকিবকে বাদ দিলে হবেনা বাংলাদে...   
7080  ববিতা যেই অভিনয়টা করলো,একজন <Gender> ভাল বাসার...   
9479                      <Gender> ভিডিও টি ভালো লাগলো।   
8973                            খুব ভালো লাগলো <Gender>   
...                                                 ...   
78    বাংলাদের খেলা আর দেখবু না <Gender> পাপন চুর কয়...   
4118  খানকির <Gender> কোন গর্ত থেকে উঠে আসছস। তোর মত...   
4587  চৈতালি <Gender> <Gender> তকে হালালা করবো আর অব...   
2416  আপনার ডিসি <Gender> এত সাধুনা যদি ভাল হত এত লু...   
3379         <Gender> তুই একটা শয়তান এবং তোর দল ও শয়তান   

                                 Gender and Name Masked  
5421  <Gender> আর বাংলার খেলাই দেখব নাসাওয়ার দে‌শে স...  
5488  আই ছিছির মন গড়া <Name> বাদ দিলে হবে

In [8]:
test

Original Sentence  \
8     দেখেছো মাগি না হিজরা বোঝা যাচ্ছে না। দেখে মনে ...   
32                          মাগি খোর সাব্বির কে বাদ দাও   
40    পাপন সাহেব উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ ...   
41    পাপন সাহেব উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ ...   
42    পাপন সাহেব উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ ...   
...                                                 ...   
9716  সেই কাগজ কোথায় বেটা চাপা মেরে খাস দশ হাজার টাক...   
9831                 সব চোর হাসিনা দল হাসিনা হল ভোট চোর   
9857                                        ও একটা পাগল   
9858                                        ও একটা পাগল   
9997                     রানু পাগলি কে খমা করা উচিত নয়   

                                     Converted Sentence  \
8     দেখেছো মাইগ্যা না হিজরা বোঝা যাচ্ছে না ।  দেখে...   
32                       মাইগ্যা খোর সাব্বির কে বাদ দাও   
40    গুলশান  মেম উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ...   
41    আদৃতা  বিবি উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ...   
42    সাবিত্রী  সাহেবা উপর দিয়ে পানি ঢালে আর নিচ দিয়...   
...                                                 ...   
9716  সেই কাগজ কোথায় বেটি চাপা মেরে খাস দশ হাজার টাক...   
9831            সব চুন্নি সাদিয়া  দল সাদিয়া  হল ভোট চোর   
9857                                     ও একটা পাগলিনী   
9858                                       ও একটা পাগলী   
9997                    আহনাফ পাগলা কে খমা করা উচিত নয়   

                       Name  original_lebel  \
8                        []               1   
32              ['সাব্বির']               1   
40                 ['পাপন']               1   
41                 ['পাপন']               1   
42                 ['পাপন']               1   
...                     ...             ...   
9716                     []               0   
9831  [' হাসিনা', 'হাসিনা']               0   
9857                     []               0   
9858                     []               0   
9997              ['রানু ']               0   

      Predicted Value for Original Sentence  \
8                                         1   
32                                        1   
40                                        0   
41                                        0   
42                                        0   
...                                     ...   
9716                                      1   
9831                                      0   
9857                                      0   
9858                                      0   
9997                                      1   

      Predicted Value for ner converted  Predict Biasness  \
8                                     0                 1   
32                                    0                 1   
40                                    1                 1   
41                                    1                 1   
42                                    1                 1   
...                                 ...               ...   
9716                                  0                 1   
9831                                  1                 1   
9857                                  1                 1   
9858                                  1                 1   
9997                                  0                 1   

                                          Gender Masked  \
8     দেখেছো <Gender> না হিজরা বোঝা যাচ্ছে না। দেখে ...   
32                      <Gender> খোর সাব্বির কে বাদ দাও   
40    পাপন <Gender> উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গ...   
41    পাপন <Gender> উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গ...   
42    পাপন <Gender> উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গ...   
...                                                 ...   
9716  সেই কাগজ কোথায় <Gender> চাপা মেরে খাস দশ হাজার...   
9831       সব <Gender> হাসিনা দল হাসিনা হল ভোট <Gender>   
9857                                    ও একটা <Gender>   
9858                                    ও একটা <Gender>   
9997                  রানু <Gender> কে খমা করা উচিত নয়   

                                 Gender and Name

# Result Before Finetuning

In [9]:
x = test[ test['original_lebel'] != test['Predicted Value for Original Sentence'] ]
y = test[ test['original_lebel'] != test['Predicted Value for ner converted'] ]
a_x = 1 - (len(x)/len(test))
a_y = 1 - (len(y)/len(test))
print('Total Mismatched Prediction Between Original Sentence Inference and Original Label: ', len(x), 'Accuracy: ', a_x)
print('Total Mismatched Prediction Between NERSentence Inference and Original Labell', len(y), 'Accuracy: ',a_y )
print('Average Accuracy: ', (a_x + a_y)/2)

Total Mismatched Prediction Between Original Sentence Inference and Original Label:  88 Accuracy:  0.8323809523809524
Total Mismatched Prediction Between NERSentence Inference and Original Labell 437 Accuracy:  0.16761904761904767
Average Accuracy:  0.5


# Approach 2 (Minimizing Joint Loss)

## Load Pretrained Model

In [10]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torchvision
import torchvision.transforms as transform
from torch.utils.data import DataLoader
from transformers import AutoTokenizer, AutoModelForMaskedLM, BertConfig
import pandas as pd
import numpy as np
import transformers
import torch
import torch.nn as nn
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
import torch.optim as optim
import torch.nn.functional as F
from torchsummary import summary
from tqdm import tqdm
from tqdm import tqdm
import torch
import torch.optim as optim
import torch.nn.functional as F
from collections import OrderedDict
from datetime import datetime
from transformers import get_linear_schedule_with_warmup, AdamW

def load_transformer_based_model(model_path):
    tokenizer = AutoTokenizer.from_pretrained(model_path)
    model = AutoModelForMaskedLM.from_pretrained(model_path ,output_hidden_states=True)
    return tokenizer, model
model_path = "Hate-speech-CNERG/bengali-abusive-MuRIL"
tokenizer, b_model = load_transformer_based_model(model_path)
print('Total Pretrained tokens: ',len(tokenizer.get_vocab()))
tokenizer.add_tokens(['<Name>' ,'<Gender>'])
b_model.resize_token_embeddings(len(tokenizer))
print('Total number of tokens after adding the new ones: ',len(tokenizer.get_vocab()))

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/547 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/3.16M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/686 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/950M [00:00<?, ?B/s]

Some weights of BertForMaskedLM were not initialized from the model checkpoint at Hate-speech-CNERG/bengali-abusive-MuRIL and are newly initialized: ['cls.predictions.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Total Pretrained tokens:  197285
Total number of tokens after adding the new ones:  197287


## Creating Custom Data Loader

In [11]:
class BertDataset(Dataset):
    def __init__(self, data, tokenizer,max_length):
        super(BertDataset, self).__init__()

        self.train_csv= data
        self.tokenizer=tokenizer
        self.target=self.train_csv.iloc[:,1]
        self.max_length=max_length

    def __len__(self):
        return len(self.train_csv)

    def __getitem__(self, index):

        text1 = self.train_csv.iloc[index,0] #0th column Original Text
        text2 = self.train_csv.iloc[index,1] #1st column NER Converted Text

        inputs = self.tokenizer.batch_encode_plus(
            [text1, text2] ,
            pad_to_max_length=True,
            add_special_tokens=True,
            return_attention_mask=True,
            max_length=self.max_length,
            truncation = True
        )
        ids = inputs["input_ids"]
        token_type_ids = inputs["token_type_ids"]
        masks = inputs["attention_mask"]

        return torch.tensor(ids[0], dtype=torch.long), torch.tensor(token_type_ids[0], dtype=torch.long), torch.tensor(masks[0], dtype=torch.long), torch.tensor(ids[1], dtype=torch.long), torch.tensor(token_type_ids[1], dtype=torch.long), torch.tensor(masks[1], dtype=torch.long), torch.tensor(self.train_csv.iloc[index, 3], dtype=torch.long)

BATCH_SIZE = 16

dataset_train= BertDataset(train, tokenizer, max_length=200 )
dataset_val= BertDataset( validation, tokenizer, max_length=200)
dataset_test= BertDataset(test, tokenizer, max_length=200)
train_loader=DataLoader(dataset=dataset_train,batch_size=BATCH_SIZE, shuffle=True)
validation_loader=DataLoader(dataset=dataset_val,batch_size=BATCH_SIZE, shuffle=False)
test_loader=DataLoader(dataset=dataset_test,batch_size=BATCH_SIZE, shuffle=False)

## Creating Custom Model

In [12]:
class BERT(nn.Module):
    def __init__(self, model):
        super(BERT, self).__init__()
        self.bert_model = model
        self.dropout = nn.Dropout(0.2)
        self.out = nn.Linear(768, 1)

    def forward(self,ids1, mask1, token_type_ids1, ids2, mask2, token_type_ids2, mode):
        if mode == 'training':
          ids = torch.vstack((ids1, ids2))
          mask = torch.vstack((mask1, mask2))
          token_type_ids = torch.vstack((token_type_ids1, token_type_ids2))
          o2= self.bert_model(ids,mask,token_type_ids).hidden_states[0]
          o2= o2.max(dim=1).values
          original_embedding, ner_embedding = torch.vsplit(o2, 2)
          # print(original_embedding.shape, ner_embedding.shape)
          o2 = self.dropout(original_embedding)
          out= self.out(o2)
          # print(o2.shape)

          return out, original_embedding, ner_embedding

        if mode == 'inference':
          o2= self.bert_model(ids1, mask1, token_type_ids1).hidden_states[0]
          oe= o2.max(dim=1).values
          o2 = self.dropout(oe)
          out= self.out(o2)
          return out, oe

masked_model=BERT(b_model)

In [ ]:
#debug
i1, t1,m1,i2,t2,m2,l = next(iter(train_loader))
print(i1.shape)
pred, oe, nere = masked_model(i1, t1,m1,i2,t2,m2, 'training')
print(pred.shape, oe.shape, nere.shape)
pred, oe = masked_model(i1, t1,m1,None,None,None, 'inference')
print(pred.shape, oe.shape)

torch.Size([16, 200])


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2699: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


torch.Size([16, 1]) torch.Size([16, 768]) torch.Size([16, 768])
torch.Size([16, 1]) torch.Size([16, 768])


## Creating Utility Class for Tracking Training Stat

In [13]:
from collections import OrderedDict
from collections import namedtuple
from itertools import product
import json
from torch.utils.tensorboard import SummaryWriter
import time
import torchvision
import pandas as pd
import torch
from IPython.display import display
from IPython.display import clear_output

class RunBuilder():
    @staticmethod
    def get_runs(params):
        Run = namedtuple('Run', params.keys())


        runs = []
        for v in product(*params.values()):
            runs.append(Run(*v))


        return runs


class RunManager():
    def __init__(self):
        self.epoch_count = 0
        self.epoch_ce_loss = 0
        self.epoch_sim_loss = 0
        self.epoch_loss = 0
        self.epoch_num_correct = 0
        self.epoch_start_time = None

        self.epoch_valid_ce_loss = 0.0
        self.epoch_valid_sim_loss = 0.0
        self.epoch_valid_loss = 0.0
        self.epoch_num_valid_correct = 0

        self.run_params = None
        self.run_count = 0
        self.run_data = []
        self.run_start_time = None

        self.network = None
        self.loader = None
        self.validation_loader = None
        self.tb = None

    def begin_run(self, run, network, loader, validation_loader):
        self.run_start_time = time.time()

        self.run_params = run
        self.run_count += 1

        self.network = network
        self.loader = loader
        self.validation_loader = validation_loader
        self.tb = SummaryWriter(comment=f'-{run}')



    def end_run(self):
        self.tb.close()
        self.epoch_count = 0

    def begin_epoch(self):
        self.epoch_start_time = time.time()
        self.epoch_count += 1
        self.epoch_loss = 0
        self.epoch_ce_loss = 0
        self.epoch_sim_loss = 0
        self.epoch_num_correct = 0
        self.epoch_valid_ce_loss = 0
        self.epoch_valid_sim_loss = 0
        self.epoch_valid_loss = 0
        self.epoch_num_valid_correct = 0

    def end_epoch(self):
        epoch_duration = time.time() - self.epoch_start_time
        run_duration = time.time() - self.run_start_time

        ce_loss = self.epoch_ce_loss/len(self.loader.dataset)
        sim_loss = self.epoch_sim_loss/len(self.loader.dataset)
        loss = self.epoch_loss/len(self.loader.dataset)
        accuracy = self.epoch_num_correct/len(self.loader.dataset)
        val_ce_loss = self.epoch_valid_ce_loss/len(self.validation_loader.dataset)
        val_sim_loss = self.epoch_valid_sim_loss/len(self.validation_loader.dataset)
        val_loss = self.epoch_valid_loss/len(self.validation_loader.dataset)
        val_accuracy = self.epoch_num_valid_correct/len(self.validation_loader.dataset)

        self.tb.add_scalar('CE Loss', ce_loss, self.epoch_count)
        self.tb.add_scalar('Sim Loss', sim_loss, self.epoch_count)
        self.tb.add_scalar('Loss', loss, self.epoch_count)
        self.tb.add_scalar('Accuracy', accuracy, self.epoch_count)
        self.tb.add_scalar('Validation CE Loss', val_ce_loss, self.epoch_count)
        self.tb.add_scalar('Validation Sim Loss', val_sim_loss, self.epoch_count)
        self.tb.add_scalar('Validation Loss', val_loss, self.epoch_count)
        self.tb.add_scalar('Validation Accuracy', val_accuracy, self.epoch_count)

        for name, param in self.network.named_parameters():
            self.tb.add_histogram(name, param, self.epoch_count)

        results = OrderedDict()
        results["run"] = self.run_count
        results["epoch"] = self.epoch_count
        results["ce_loss"] = ce_loss
        results["sim_loss"] = sim_loss
        results["loss"] = loss
        results["accuracy"] = accuracy
        results["validation ce loss"] = val_ce_loss
        results["validation sim loss"] = val_sim_loss
        results["validation loss"] = val_loss
        results["validation accuracy"] = val_accuracy
        results["epoch duration"] = epoch_duration
        results["run duration"] = run_duration
        for k,v in self.run_params._asdict().items(): results[k] = v
        self.run_data.append(results)
        df = pd.DataFrame.from_dict(self.run_data, orient='columns')

        clear_output(wait=True)
        display(df)

    def track_loss(self, ce_loss, sim_loss, loss):
        self.epoch_ce_loss += ce_loss.item()#*self.loader.batch_size
        self.epoch_sim_loss += sim_loss.item()#*self.loader.batch_size
        self.epoch_loss += loss.item()#*self.loader.batch_size

    def track_num_correct(self, preds, labels):
        self.epoch_num_correct += self._get_num_correct(preds, labels)

    def track_validation_loss(self, ce_loss, sim_loss, loss):
        self.epoch_valid_ce_loss += ce_loss.item()#*self.loader.batch_size
        self.epoch_valid_sim_loss += sim_loss.item()#*self.loader.batch_size
        self.epoch_valid_loss += loss.item()#*self.loader.batch_size

    def track_num_validation_correct(self, preds, labels):
        self.epoch_num_valid_correct += self._get_num_correct(preds, labels)

    @torch.no_grad()
    def _get_num_correct(self, preds, labels):
        return torch.where(preds >= 0, 1, 0).eq(labels).sum().item()

    def save(self, fileName):
        pd.DataFrame.from_dict(
            self.run_data,
            orient='columns').to_csv(rf'{fileName}.csv')


## Creating Training Loop

In [ ]:
SAVE_MODEL = True
def my_trainer(train_loader, validation_loader, network, LR = 1e-5 ,epochs = 5, BATCH_SIZE = 16,  fresh_training = True, validation = True):
    params = OrderedDict(
        lr = [LR],
        batch_size =[BATCH_SIZE],
        device = ['cuda' if torch.cuda.is_available() else 'cpu'],
    )

    m = RunManager()
    for run in RunBuilder.get_runs(params):
        device = torch.device(run.device)
        network = network.to(device)
        # optimizer = optim.Adam(network.parameters(), lr=run.lr)

        loss_fn = nn.BCEWithLogitsLoss()
        loss_fn_2 = nn.CosineSimilarity()

        total_steps = len(train_loader) * epochs
        optimizer = optim.Adam(network.parameters(), lr= run.lr)

        scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps = 0, num_training_steps = total_steps)
        if not fresh_training:
            load_model(network, optimizer, PATH = '')
        m.begin_run(run, network, train_loader, validation_loader)
        for epoch in range(epochs):
            network.train(True)
            print(f'Epoch {epoch + 1} : ', end = '\t')
            m.begin_epoch()
            for batch in tqdm(train_loader):
                input_ids1, token_type_ids1, attention_masks1, input_ids2, token_type_ids2, attention_masks2, labels = batch
                input_ids1 = input_ids1.to(device)
                token_type_ids1 = token_type_ids1.to(device)
                attention_masks1 = attention_masks1.to(device)

                input_ids2 = input_ids2.to(device)
                token_type_ids2 = token_type_ids2.to(device)
                attention_masks2 = attention_masks2.to(device)

                labels = labels.type(torch.LongTensor)
                labels = labels.to(device)

                preds,original_hidden_states, ner_hidden_states = network(input_ids1, attention_masks1, token_type_ids1, input_ids2, attention_masks2, token_type_ids2, 'training')
                labels = labels.type_as(preds).view(-1, 1)
                # print(labels.shape)
                # print('----------')
                # print(preds.shape)


                loss1 = loss_fn(preds, labels)
                loss2 = 1 - torch.mean(torch.abs(loss_fn_2(original_hidden_states,ner_hidden_states)))
                loss = loss1 + loss2
                # print(preds.shape, labels.shape)
                # print(preds, labels)


                optimizer.zero_grad()
                loss.backward()
                torch.nn.utils.clip_grad_norm_(network.parameters(), 1.0)
                optimizer.step()
                scheduler.step()


                m.track_loss(loss1, loss2, loss)
                m.track_num_correct(preds, labels)


            network.eval()
            for batch in tqdm(validation_loader):
                input_ids1, token_type_ids1, attention_masks1, input_ids2, token_type_ids2, attention_masks2, labels = batch
                input_ids1 = input_ids1.to(device)
                token_type_ids1 = token_type_ids1.to(device)
                attention_masks1 = attention_masks1.to(device)
                input_ids2 = input_ids2.to(device)
                token_type_ids2 = token_type_ids2.to(device)
                attention_masks2 = attention_masks2.to(device)

                labels = labels.type(torch.LongTensor)
                labels = labels.to(device)
                with torch.no_grad():
                    preds,original_hidden_states, ner_hidden_states = network(input_ids1, attention_masks1, token_type_ids1, input_ids2, attention_masks2, token_type_ids2, 'training')
                    labels = labels.type_as(preds).view(-1, 1)
                    loss1 = loss_fn(preds, labels)
                    loss2 = 1 - torch.mean(torch.abs(loss_fn_2(original_hidden_states,ner_hidden_states)))
                    loss = loss1 + loss2
                    m.track_validation_loss(loss1, loss2, loss)
                    m.track_num_validation_correct(preds, labels)
                # break #not doing validation here




            m.end_epoch()
            network.train(False)
        m.end_run()
    if SAVE_MODEL == True:
        save_model(network, optimizer)

    s = datetime.now().strftime("%d-%m-%Y %I:%M:%p").replace(" ", "_").replace(":", "_")
    PATH  = rf'results_{s}'
    m.save(PATH)
    return


def save_model(network, optimizer):
    s = datetime.now().strftime("%d-%m-%Y %I:%M:%p").replace(" ", "_").replace(":", "_")
    PATH  = rf'/content/drive/MyDrive/#Research/# GB/saved_model/HateSpeech_A2.pth'
    torch.save({
    'model_state_dict': network.state_dict(),
    'optimizer_state_dict': optimizer.state_dict(),
    }, PATH)
    print(f'Saved model and optimizer at {PATH}')
    return

def load_model(network, optimizer, PATH ):
    checkpoint = torch.load(PATH)
    network.load_state_dict(checkpoint['model_state_dict'])
    if optimizer is not None:
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        print(rf'Loaded model and optimizer from {PATH}')
    else:
        print(rf'Loaded model from {PATH}')

    return

def get_parameter_info(network, details = False):
    print('Total parameters:' ,(sum(p.numel() for p in network.parameters())))
    print('Total trainable parameters:' ,(sum(p.numel() for p in network.parameters() if p.requires_grad)))
    if details:
        print('---------------------------------\nDetailed Parameter Info: ')

        for name, parameter in network.named_parameters():
            print('name, parameter.requires_grad, parameter.is_cuda, parameter.size(): ', name, parameter.requires_grad, parameter.is_cuda, parameter.size())
            print('---------------------------------')
    return


if finetuning:
  my_trainer(train_loader, validation_loader, masked_model, 0.0001, epochs = 15, BATCH_SIZE = 16, fresh_training = True)

run  epoch   ce_loss  sim_loss      loss  accuracy  validation ce loss  \
0     1      1  0.033923  0.001251  0.035174  0.749310            0.024825   
1     1      2  0.019641  0.001292  0.020932  0.881819            0.018449   
2     1      3  0.014286  0.001071  0.015357  0.914421            0.015574   
3     1      4  0.011090  0.000895  0.011985  0.938609            0.013719   
4     1      5  0.008836  0.000773  0.009610  0.953070            0.012839   
5     1      6  0.007172  0.000683  0.007855  0.962535            0.012481   
6     1      7  0.005951  0.000617  0.006567  0.970553            0.012115   
7     1      8  0.004941  0.000564  0.005505  0.978441            0.011763   
8     1      9  0.004310  0.000521  0.004831  0.981859            0.011703   
9     1     10  0.003718  0.000486  0.004204  0.983305            0.011588   
10    1     11  0.003303  0.000459  0.003762  0.986854            0.011720   
11    1     12  0.002921  0.000441  0.003362  0.988432            0.011791   
12    1     13  0.002660  0.000423  0.003083  0.988826            0.011957   
13    1     14  0.002532  0.000415  0.002947  0.991061            0.011836   
14    1     15  0.002600  0.000414  0.003014  0.990009            0.011822   

    validation sim loss  validation loss  validation accuracy  epoch duration  \
0              0.000918         0.025743             0.852709      645.320421   
1              0.000732         0.019180             0.896896      647.660867   
2              0.000554         0.016127             0.908469      646.786951   
3              0.000451         0.014170             0.918464      646.933020   
4              0.000381         0.013220             0.924776      646.352629   
5              0.000335         0.012816             0.923198      646.981617   
6              0.000300         0.012414             0.925829      648.064451   
7              0.000272         0.012035             0.926881      647.198774   
8              0.000251         0.011954             0.925302      647.436836   
9              0.000234         0.011821             0.928985      647.532099   
10             0.000221         0.011942             0.928985      648.129358   
11             0.000212         0.012003             0.928985      646.714989   
12             0.000205         0.012162             0.932141      646.863210   
13             0.000201         0.012037             0.930037      647.843838   
14             0.000200         0.012022             0.930037      649.893287   

    run duration      lr  batch_size device  
0     645.322423  0.0001          16   cuda  
1    1300.003462  0.0001          16   cuda  
2    1952.464708  0.0001          16   cuda  
3    2606.714219  0.0001          16   cuda  
4    3258.659688  0.0001          16   cuda  
5    3912.417696  0.0001          16   cuda  
6    4566.752579  0.0001          16   cuda  
7    5219.850153  0.0001          16   cuda  
8    5873.207162  0.0001          16   cuda  
9    6526.553511  0.0001          16   cuda  
10   7181.931809  0.0001          16   cuda  
11   7834.512912  0.0001          16   cuda  
12   8487.095824  0.0001          16   cuda  
13   9140.976140  0.0001          16   cuda  
14   9798.314974  0.0001          16   cuda

Saved model and optimizer at /content/drive/MyDrive/#Research/# GB/saved_model/HateSpeech_A2.pth


## Load Saved Model

In [16]:
#Load Model
from tqdm import tqdm
import torch
import torch.optim as optim
import torch.nn.functional as F
from collections import OrderedDict
from datetime import datetime
from transformers import get_linear_schedule_with_warmup, AdamW

def load_model(network, optimizer, PATH ):
    checkpoint = torch.load(PATH, map_location=torch.device('cpu'))
    network.load_state_dict(checkpoint['model_state_dict'])
    if optimizer is not None:
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        print(rf'Loaded model and optimizer from {PATH}')
    else:
        print(rf'Loaded model from {PATH}')

    return


if load_and_run:
  load_model(masked_model, None, PATH = '/content/drive/MyDrive/#Research/# GB/saved_model/HateSpeech_A2.pth')

Loaded model from /content/drive/MyDrive/#Research/# GB/saved_model/HateSpeech_A2.pth


## Inference

In [17]:
def get_prediction(data_loader, network, choice = 'original'):
  device = 'cuda' if torch.cuda.is_available() else 'cpu'
  device = torch.device(device)
  network = network.to(device)
  network.eval()
  l = []
  emb = []
  for batch in tqdm(data_loader):
    input_ids1, token_type_ids1, attention_masks1, input_ids2, token_type_ids2, attention_masks2, labels = batch
    input_ids1 = input_ids1.to(device)
    token_type_ids1 = token_type_ids1.to(device)
    attention_masks1 = attention_masks1.to(device)
    input_ids2 = input_ids2.to(device)
    token_type_ids2 = token_type_ids2.to(device)
    attention_masks2 = attention_masks2.to(device)
    labels = labels.type(torch.LongTensor)
    labels = labels.to(device)
    with torch.no_grad():
        if choice == 'original':
          preds, hidden_states = network(input_ids1, attention_masks1,token_type_ids1, None, None, None, 'inference')
        else:
          preds, hidden_states = network(input_ids2, attention_masks2,token_type_ids2, None, None, None, 'inference')

        labels = labels.type_as(preds).view(-1, 1)
        preds =  torch.where(preds >= 0, 1, 0)
        l.append(preds)
        emb.append(hidden_states)
  return l, torch.vstack(emb).cpu().numpy()
dataset_test= BertDataset(test, tokenizer, max_length=200)
test_loader=DataLoader(dataset=dataset_test,batch_size=16, shuffle = False)
p, emb_org = get_prediction(test_loader, masked_model, 'original')
test['a2_original_pred'] = [x[0] for pred in p for x in pred.tolist()]
p, emb_ner = get_prediction(test_loader, masked_model, 'ner')
test['a2_ner_pred'] = [x[0] for pred in p for x in pred.tolist()]
test

  0%|          | 0/33 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2699: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(
100%|██████████| 33/33 [00:12<00:00,  2.57it/s]
<ipython-input-17-5688313f06bc>:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test['a2_original_pred'] = [x[0] for pred in p for x in pred

Original Sentence  \
8     দেখেছো মাগি না হিজরা বোঝা যাচ্ছে না। দেখে মনে ...   
32                          মাগি খোর সাব্বির কে বাদ দাও   
40    পাপন সাহেব উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ ...   
41    পাপন সাহেব উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ ...   
42    পাপন সাহেব উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ ...   
...                                                 ...   
9716  সেই কাগজ কোথায় বেটা চাপা মেরে খাস দশ হাজার টাক...   
9831                 সব চোর হাসিনা দল হাসিনা হল ভোট চোর   
9857                                        ও একটা পাগল   
9858                                        ও একটা পাগল   
9997                     রানু পাগলি কে খমা করা উচিত নয়   

                                     Converted Sentence  \
8     দেখেছো মাইগ্যা না হিজরা বোঝা যাচ্ছে না ।  দেখে...   
32                       মাইগ্যা খোর সাব্বির কে বাদ দাও   
40    গুলশান  মেম উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ...   
41    আদৃতা  বিবি উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ...   
42    সাবিত্রী  সাহেবা উপর দিয়ে পানি ঢালে আর নিচ দিয়...   
...                                                 ...   
9716  সেই কাগজ কোথায় বেটি চাপা মেরে খাস দশ হাজার টাক...   
9831            সব চুন্নি সাদিয়া  দল সাদিয়া  হল ভোট চোর   
9857                                     ও একটা পাগলিনী   
9858                                       ও একটা পাগলী   
9997                    আহনাফ পাগলা কে খমা করা উচিত নয়   

                       Name  original_lebel  \
8                        []               1   
32              ['সাব্বির']               1   
40                 ['পাপন']               1   
41                 ['পাপন']               1   
42                 ['পাপন']               1   
...                     ...             ...   
9716                     []               0   
9831  [' হাসিনা', 'হাসিনা']               0   
9857                     []               0   
9858                     []               0   
9997              ['রানু ']               0   

      Predicted Value for Original Sentence  \
8                                         1   
32                                        1   
40                                        0   
41                                        0   
42                                        0   
...                                     ...   
9716                                      1   
9831                                      0   
9857                                      0   
9858                                      0   
9997                                      1   

      Predicted Value for ner converted  Predict Biasness  \
8                                     0                 1   
32                                    0                 1   
40                                    1                 1   
41                                    1                 1   
42                                    1                 1   
...                                 ...               ...   
9716                                  0                 1   
9831                                  1                 1   
9857                                  1                 1   
9858                                  1                 1   
9997                                  0                 1   

                                          Gender Masked  \
8     দেখেছো <Gender> না হিজরা বোঝা যাচ্ছে না। দেখে ...   
32                      <Gender> খোর সাব্বির কে বাদ দাও   
40    পাপন <Gender> উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গ...   
41    পাপন <Gender> উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গ...   
42    পাপন <Gender> উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গ...   
...                                                 ...   
9716  সেই কাগজ কোথায় <Gender> চাপা মেরে খাস দশ হাজার...   
9831       সব <Gender> হাসিনা দল হাসিনা হল ভোট <Gender>   
9857                                    ও একটা <Gender>   
9858                                    ও একটা <Gender>   
9997                  রানু <Gender> কে খমা করা উচিত নয়   

                                 Gender and Name

## Result of Approach 2

In [18]:
x = sum(test['original_lebel'] != test['a2_original_pred'])
print('For Original text:\nTotal test data: ', len(test),'Total mismatch: ', x,'Accuracy: ', 1 - (x/len(test)) )
x = sum(test['original_lebel'] != test['a2_ner_pred'])
print('For NER Converted text:\nTotal test data: ', len(test),'Total mismatch: ', x,'Accuracy: ', 1 - (x/len(test)))
print('Bias: ', sum(test['a2_ner_pred'] != test['a2_original_pred']))

For Original text:
Total test data:  525 Total mismatch:  114 Accuracy:  0.7828571428571429
For NER Converted text:
Total test data:  525 Total mismatch:  191 Accuracy:  0.6361904761904762
Bias:  119


## Sentence Embedding Visualization for Original Sentence and NER Converted Sentence

In [ ]:
#for visualizing training data embedding
dataset_train= BertDataset(train, tokenizer, max_length=200)
train_loader=DataLoader(dataset=dataset_train,batch_size=16, shuffle = False)
p, emb_ori = get_prediction(train_loader, masked_model, 'original')
p, emb_ner = get_prediction(train_loader, masked_model, 'ner')

  0%|          | 0/476 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2699: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(
100%|██████████| 476/476 [03:25<00:00,  2.32it/s]


In [ ]:
from sklearn.manifold import TSNE
import plotly.express as px

tsne_cls = TSNE(n_components=2, random_state=42).fit_transform(emb_ori)

labels = train['original_lebel']   # Extract labels
review_texts = train['Original Sentence']  # Extract review texts

# Prepare the data for Plotly plots
plot_data_cls = {'t-SNE Dimension 1': tsne_cls[:, 0],
                 't-SNE Dimension 2': tsne_cls[:, 1],
                 'Label': labels,
                 'Text': review_texts}

# Customize colorbar to show integer labels
colorbar_tickvals = list(range(1, 6))
colorbar_ticktext = [str(val) for val in colorbar_tickvals]

# Plotting with Plotly - [CLS] Token Embeddings
fig_cls = px.scatter(plot_data_cls, x='t-SNE Dimension 1', y='t-SNE Dimension 2',
                     color='Label', hover_data={'t-SNE Dimension 1': False, 't-SNE Dimension 2': False, 'Text': True})


fig_cls.update_layout(title='t-SNE of Embeddings Original Training Data with Labels', height=700,  font=dict(
        size=20,
))
fig_cls.update_traces(marker=dict(size=10, opacity=0.9))

fig_cls.update_layout(coloraxis_colorbar=dict(
    tickvals=colorbar_tickvals,
    ticktext=colorbar_ticktext
))

fig_cls.show()


In [ ]:
from sklearn.manifold import TSNE
import plotly.express as px

tsne_cls = TSNE(n_components=2, random_state=42).fit_transform(emb_ner)

labels = train['original_lebel']   # Extract labels
review_texts = train['Converted Sentence']  # Extract review texts

# Prepare the data for Plotly plots
plot_data_cls = {'t-SNE Dimension 1': tsne_cls[:, 0],
                 't-SNE Dimension 2': tsne_cls[:, 1],
                 'Label': labels,
                 'Text': review_texts}

# Customize colorbar to show integer labels
colorbar_tickvals = list(range(1, 6))
colorbar_ticktext = [str(val) for val in colorbar_tickvals]

# Plotting with Plotly - [CLS] Token Embeddings
fig_cls = px.scatter(plot_data_cls, x='t-SNE Dimension 1', y='t-SNE Dimension 2',
                     color='Label', hover_data={'t-SNE Dimension 1': False, 't-SNE Dimension 2': False, 'Text': True})


fig_cls.update_layout(title='t-SNE of Embeddings NER Converted Training Data with Labels', height=700,  font=dict(
        size=20,
))
fig_cls.update_traces(marker=dict(size=10, opacity=0.9))

fig_cls.update_layout(coloraxis_colorbar=dict(
    tickvals=colorbar_tickvals,
    ticktext=colorbar_ticktext
))

fig_cls.show()


In [ ]:
test.to_csv('/content/drive/MyDrive/#Research/# GB/hateSpeech_reSult_a2.csv', index = False)